In [1]:
# hidden
import environment as env
env.initialize()

### Verificación de la alineación principal del dique 

Este ejemplo continuará a partir de los estados caracerísticos de altura de ola significantes $H_s$ guardados al final del apartado [Distribución de extremos de la variable principal y obtención de su valor para un determinado periodo de retorno](cl_regimen_extremal_04.ipynb) para un periodo de retorno $T_r = 200$ años y los valores correspondientes de periodo pico obtenidos en el apartado [Funciones de regresión para la caracterización de las variables no predominantes](cl_regresion_Tp_01.ipynb). 

Realizando el mismo procediemiento presentado en [Funciones de regresión para la caracterización de las variables no predominantes](cl_regresion_Tp_01.ipynb) para el periodo pico, se obtienen los valores correspondientes a la dirección media del oleaje $\theta$ [](cl_regresion_Dh_02.ipynb), velocidad de viento $U$ [](cl_regresion_Vv_03.ipynb), dirección media del viento $\theta_U$ [](cl_regresion_Dv_04.ipynb), nivel de mar $\eta_{Mme}, \eta_{Mas}$ para un periodo de retorno $T_r = 200$ años y los intervalos de confianza.

En este ejemplo se realiza la verificación de la fiabilidad de la alineación principal de un dique de abrigo tipo mixto con berma baja de protección (Tipo C, LMB).

Las funciones que se utilizan son:

- verificacion.verificacion_mf.verificacion_simultanea


In [2]:
# imports Anaconda
from __future__ import division
import os
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from IPython.display import HTML

# imports ROM 1.1
from verificacion.verificacion_mf import verificacion_simultanea

dir_data = os.path.join(env.data_path, 'clima')
dir_output_ver = os.path.join(env.output_path, 'verificacion')

df_hs_tp = pd.read_pickle(os.path.join(dir_data, 'out_reg_extremal__Hs_Tp_tr.pkl'))      
df_hs_dh = pd.read_pickle(os.path.join(dir_data, 'out_reg_extremal__Hs_Dh_tr.pkl'))        
df_hs_vv = pd.read_pickle(os.path.join(dir_data, 'out_reg_extremal__Hs_U_tr.pkl'))        
df_hs_dv = pd.read_pickle(os.path.join(dir_data, 'out_reg_extremal__Hs_Du_tr.pkl')) 
df_hs_mme = pd.read_pickle(os.path.join(dir_data, 'out_reg_extremal__Hs_Mme_tr.pkl'))        
df_hs_mas = pd.read_pickle(os.path.join(dir_data, 'out_reg_extremal__Hs_Mas_tr.pkl'))        

Según el reparto de probabilidad de fallo considerado y una vida útil de la obra de $V=25$ años, se obtienen parejas de balores ($T_R, \beta$). Seleccionado un período de retorno de 200 años, el valor de $\beta$ en las ecuaciones de verificación debe ser mayor que 0.58. 

Se seleccionan los valores de los estados caracteristicos para $T_r = 200$ años:

In [3]:
tr = 200
pos_tr = df_hs_tp['Tr']==tr

hs, tp, dh = df_hs_tp.loc[pos_tr, 'Hs'].values[0], df_hs_tp.loc[pos_tr, 'Tp'].values[0],\
             df_hs_dh.loc[pos_tr, 'Dh'].values[0] 
vv, dv = df_hs_vv.loc[pos_tr, 'U'].values[0], df_hs_dv.loc[pos_tr, 'Du'].values[0]
mme, mas = df_hs_mme.loc[pos_tr, 'Mme'].values[0], df_hs_mas.loc[pos_tr, 'Mmas'].values[0]

estados = pd.DataFrame({'hs' : np.repeat(hs, 3), 'tp' : np.repeat(tp, 3), 'dh' : np.repeat(dh, 3), \
                        'vv' : np.repeat(vv, 3),'dv' : np.repeat(dv, 3), 'marea': [-mas + mme, mme, mas + mme]})

In [4]:
estados

dh          dv        hs     marea         tp         vv
0  263.808  274.238777  4.709996 -1.014432  17.770473  21.457686
1  263.808  274.238777  4.709996  0.572667  17.770473  21.457686
2  263.808  274.238777  4.709996  2.159766  17.770473  21.457686

Entradas de usuario - datos de partida y parámetros de diseño del dique: 

In [5]:
""" REQUISITOS DE PROYECTO """
vida = 25
pc_f = 0.1
beta_min = 1.8
nivel_averia = 'IA'

""" DATOS DE PARTIDA """
# Caracteristicas del emplazamiento
profundidad = 17.75

""" CARACTERISTICAS DEL DIQUE """
tipo = 'C1'
par_dique = {}
par_dique['b'] = 12
par_dique['d'] = 0.25
par_dique['d_mean'] = 0.25
par_dique['d_var'] = 0.05
par_dique['dens_rel'] = 1.7
par_dique['h_b'] = 4

par_dique['f_mt'] = 6
par_dique['b_b'] = 3
par_dique['alpha_t'] = 1.5

par_dique['d_b'] = 0.65
par_dique['d_b_mean'] = 0.65
par_dique['d_b_var'] = 0.05
par_dique['pieza'] = True
par_dique['ns'] = 0.4

# Dique talud
par_dique['tipo_pieza'] = 'E' # tipo pieza: E: escollera; C: cubo; T:tetrapodo

# Rozamiento
par_dique['mu_mean'] = 0.6
par_dique['mu_var'] = 0.02

lista_modos_fallo = ['deslizamiento', 'vuelco', 'estabilidad_berma']

El comportamiento hidráulico de la sección en los estados analizados se caracteriza mediante el coeficiente de reflexión $K_R$, el coeficiente de transmisión $K_T$, el coeficiente de disipación $D^*$ y la fase de la reflexión $\phi$. Éstos dependen de las características de los agentes y del parámetro de dispersión $A_{eq}/L^2$ donde $A_{eq}$ es el área equivalente de la sección, correspondiente al área de material poroso por debajo del nivel del mar de referencia. 

Para cada modo y estado se devuelve información sobre el valor medio del margen de seguridad ($\mu_S$), su desviación típica ($\sigma_S$) y el coeficiente $\beta$ que expresa el número de desviaciones típicas que separa el valor medio del margen de seguridad de la situación de fallo $S = 0$.

In [6]:
# Variables derivadas
par_dique['a_eq_b'] = par_dique['b_b'] * par_dique['f_mt'] + 0.5 * par_dique['f_mt'] * par_dique['alpha_t'] * \
                                                             par_dique['f_mt']
par_dique['a_eq'] = par_dique['a_eq_b'] + par_dique['b'] * par_dique['h_b']

par_dique['x4'] = par_dique['b_b'] + par_dique['alpha_t'] * par_dique['f_mt']
par_dique['x2'] = par_dique['x4'] / 3
par_dique['x3'] = par_dique['x4'] * 2 / 3


modos_fallo = []
info_mf = []

list_df_comp, list_df_fallo = list(), list()
for ei2, estado in estados.iterrows():
    par_dique['f_c'] = 6 - estado['marea']
    
    df_modos_fallo, d_info_mf = verificacion_simultanea(estado, lista_modos_fallo, profundidad, tipo, par_dique,
                                                        nivel_averia)        
    # Comportamiento hidráulico
    df_out = pd.DataFrame({'h': d_info_mf['prof'], 'k_r':d_info_mf['k_r'], 'k_t':d_info_mf['k_t'], 'dis': d_info_mf['dis'], 'phi': d_info_mf['phi']}, index=[ei2])
    list_df_comp.append(df_out)

    # Modos de fallo
    df_out_ver = pd.DataFrame({'h': d_info_mf['prof'], 'beta':df_modos_fallo['beta'], 's_mean':df_modos_fallo['mean'], 's_dest': df_modos_fallo['dest'], 'estado':ei2})
    list_df_fallo.append(df_out_ver)

# Guardar html y df
df_outf_compo = pd.concat(list_df_comp)
r_ds = os.path.join(env.output_path, 'verificacion', 'salida_comportamiento__' + tipo + '.html')
df_outf_compo.to_html(r_ds, sparsify=False)
df_outf_compo.to_pickle(os.path.join(env.output_path, 'verificacion', 'salida_comportamiento__' + tipo + '.pkl'))

# Guardar html y df
df_outf_ver = pd.concat(list_df_fallo)
r_ds = os.path.join(env.output_path, 'verificacion', 'salida_verificacion__' + tipo + '.html')
df_outf_ver.to_html(r_ds, sparsify=False)
df_outf_ver.to_pickle(os.path.join(env.output_path, 'verificacion', 'salida_verificacion__' + tipo + '.pkl'))

#### Comportamiento hidráulico

In [8]:
# Mostrar en pantalla
r_ds = os.path.join(env.output_path, 'verificacion', 'salida_comportamiento__' + tipo + '.html')
HTML(filename=r_ds)

#### Verificación de modos de fallo

In [9]:
r_ds1 = os.path.join(env.output_path, 'verificacion', 'salida_verificacion__' + tipo + '.html')
HTML(filename=r_ds1)